# Bigquery anomaly detection with Gdelt

In this notebook we will query the Gdelt Global Entity Graph and find which entities are anomolus based on BQ ARIMA+ model

In [1]:
import json
#set params
BEGIN = "2021-03-01"
END = "2021-04-30"

HEIGHT = 400
WIDTH = 400

bq_params = {"BEGIN": BEGIN, "END": END}
bq_params = json.dumps(bq_params, indent=4, sort_keys=True, default=str)

### First step - get top entities by count, partitioned by day

In [2]:
%%bigquery --params {"BEGIN": "2021-03-01", "END": "2021-04-30"}

CREATE OR REPLACE TABLE cpg-cdp.trendspotting.gdelt_terms as (
WITH geg_data AS ((
    SELECT 
    groupId, 
    name, 
    a.entity as stringVal, 
    a.numMentions, 
    a.avgSalience, 
    eventTime, 
    polarity, 
    magnitude, 
    score 
    from (
    	SELECT polarity, 
        magnitude, 
        score, 
        FARM_FINGERPRINT(url) groupId, 
        CONCAT('Entity',entity.type) name, 
        FORMAT_TIMESTAMP("%Y-%m-%d", date, "UTC") eventTime, 
    	entity.mid mid FROM `gdelt-bq.gdeltv2.geg_gcnlapi`, UNNEST(entities) entity WHERE entity.mid is not null 
       and lang='en' and DATE(date) >= @BEGIN and DATE(date) <= @END
  ) b JOIN (
     SELECT APPROX_TOP_COUNT(entities.name, 1)[OFFSET(0)].value entity, #grab the entities from the nested json in the graph
        entities.mid mid, sum(entities.numMentions) as numMentions, 
        avg(entities.avgSalience) as avgSalience
      FROM `gdelt-bq.gdeltv2.geg_gcnlapi`, 
     unnest(entities) entities where entities.mid is not null and lang='en' 
     and DATE(date) >= @BEGIN and DATE(date) <= @END group by entities.mid
  ) a USING(mid)))
select * from 
(select *, RANK() OVER (PARTITION BY eventTime ORDER BY numMentions desc) as rank #Get ranks
from
(select stringVal, 
    name, 
    eventTime, 
    sum(numMentions) as numMentions, 
    avg(magnitude) as avgMagnitude 
    from geg_data group by 1,2,3) grouped_all) where rank < 300 #limit to top 500 entities partitioned by day - this is important and may want to report by different bands of popularity
)

Query complete after 0.06s: 100%|██████████| 14/14 [00:00<00:00, 8843.41query/s]                       


Empty DataFrame
Columns: []
Index: []

A quick check on the data shows the same structure as in the EDA

In [3]:
%%bigquery data
select * from cpg-cdp.trendspotting.gdelt_terms

Downloading: 100%|██████████| 18239/18239 [00:01<00:00, 13423.74rows/s]


In [4]:
data

stringVal                 name   eventTime  numMentions  \
0             Oscar          EntityEVENT  2021-04-27     45582688   
1             Oscar          EntityEVENT  2021-03-15     28984644   
2             Oscar          EntityEVENT  2021-04-23     39884852   
3             Oscar          EntityEVENT  2021-04-11     22419746   
4             Oscar          EntityEVENT  2021-04-25     92651768   
...             ...                  ...         ...          ...   
18234      COVID-19  EntityCONSUMER_GOOD  2021-04-15     41011017   
18235      COVID-19  EntityCONSUMER_GOOD  2021-04-06     51309804   
18236      COVID-19  EntityCONSUMER_GOOD  2021-03-19     43539681   
18237      WhatsApp  EntityCONSUMER_GOOD  2021-04-30     22751793   
18238  Donald Trump  EntityCONSUMER_GOOD  2021-04-11     29209842   

       avgMagnitude  rank  
0          8.544565   194  
1          7.160684   262  
2          8.786335   203  
3          5.824309   242  
4         11.529545   114  
...             ...   ...  
18234      8.726316   212  
18235     11.058333   174  
18236      7.095000   206  
18237     19.737977   270  
18238      8.911111   209  

[18239 rows x 6 columns]

## Overall flow visualization
Here are all the topics stacked by mentions over time - hard to interpret, so let's see what gets automatically tagged as an anomaly

In [9]:
import altair as alt
alt.data_transformers.disable_max_rows()


alt.Chart(data).mark_area().encode(
    alt.X('eventTime:T',
        axis=alt.Axis(format='%Y%m%d', domain=False, tickSize=1)
    ),
    alt.Y('sum(numMentions):Q', stack='center', axis=None),
    alt.Color('stringVal:N',
        scale=alt.Scale(scheme='category20b')
    ),
    #alt.Tooltip(['numMentions','stringVal']),
).properties(
        title="Number of Mentions top Topics",
        height=HEIGHT,
        width=WIDTH*2
    ).interactive()

alt.Chart(...)

### Second step - run BQML on the data [link](https://cloud.google.com/blog/products/data-analytics/bigquery-ml-unsupervised-anomaly-detection)

In [ ]:
%%bigquery

CREATE OR REPLACE MODEL trendspotting.gdelt_anomaly_v_1
OPTIONS(
  MODEL_TYPE='ARIMA_PLUS',
  TIME_SERIES_TIMESTAMP_COL='eventTime',
  TIME_SERIES_DATA_COL='numMentions',
  TIME_SERIES_ID_COL='stringVal',
  HOLIDAY_REGION='US' 
) AS
SELECT
  cast(eventTime as Date) as eventTime, stringVal, numMentions
FROM `cpg-cdp.trendspotting.gdelt_terms`

## Now detect anomalies on the training set

In [169]:
%%bigquery anoms
SELECT
  * 
FROM
  ML.DETECT_ANOMALIES(MODEL `trendspotting.gdelt_anomaly_v_1`,
                      STRUCT(0.99 AS anomaly_prob_threshold)) a,
    `cpg-cdp.trendspotting.gdelt_terms` b where a.stringVal = b.stringVal and a.eventTime = CAST(b.eventTime  as TIMESTAMP)

Downloading: 100%|██████████| 17685/17685 [00:01<00:00, 16299.69rows/s]


In [170]:
anoms

stringVal                 eventTime  \
0                                              AP 2021-03-01 00:00:00+00:00   
1                                              AP 2021-04-11 00:00:00+00:00   
2                                              AP 2021-03-11 00:00:00+00:00   
3                                              AP 2021-03-15 00:00:00+00:00   
4                                              AP 2021-04-01 00:00:00+00:00   
...                                           ...                       ...   
17680  Centers for Disease Control and Prevention 2021-04-09 00:00:00+00:00   
17681  Centers for Disease Control and Prevention 2021-04-20 00:00:00+00:00   
17682  Centers for Disease Control and Prevention 2021-03-30 00:00:00+00:00   
17683  Centers for Disease Control and Prevention 2021-03-16 00:00:00+00:00   
17684  Centers for Disease Control and Prevention 2021-04-03 00:00:00+00:00   

        numMentions  is_anomaly   lower_bound   upper_bound  \
0      3.319966e+09       False  2.908441e+09  3.731491e+09   
1      2.688041e+09       False  2.023297e+09  2.846347e+09   
2      3.909541e+09       False  3.449758e+09  4.272809e+09   
3      3.709317e+09       False  3.179298e+09  4.002349e+09   
4      3.856016e+09       False  3.332082e+09  4.155133e+09   
...             ...         ...           ...           ...   
17680  7.605644e+08       False  5.783087e+08  1.100858e+09   
17681  5.813854e+08       False  5.519929e+08  1.074542e+09   
17682  8.116683e+08       False  6.197556e+08  1.142305e+09   
17683  6.719213e+08       False  5.208997e+08  1.043449e+09   
17684  5.485780e+08       False  3.435423e+08  8.660919e+08   

       anomaly_probability                                 stringVal_1  \
0                 0.000000                                          AP   
1                 0.888976                                          AP   
2                 0.238575                                          AP   
3                 0.543814                                          AP   
4                 0.520455                                          AP   
...                    ...                                         ...   
17680             0.566081  Centers for Disease Control and Prevention   
17681             0.978352  Centers for Disease Control and Prevention   
17682             0.508073  Centers for Disease Control and Prevention   
17683             0.724687  Centers for Disease Control and Prevention   
17684             0.422896  Centers for Disease Control and Prevention   

                     name eventTime_1  numMentions_1  avgMagnitude  rank  
0      EntityORGANIZATION  2021-03-01     3319965958     13.160897    10  
1      EntityORGANIZATION  2021-04-11     2688040809     12.225198     9  
2      EntityORGANIZATION  2021-03-11     3909540753     12.323012     8  
3      EntityORGANIZATION  2021-03-15     3709316794     14.953408     8  
4      EntityORGANIZATION  2021-04-01     3856015801     12.627215     9  
...                   ...         ...            ...           ...   ...  
17680  EntityORGANIZATION  2021-04-09      760564416     13.250726    37  
17681  EntityORGANIZATION  2021-04-20      581385408     12.619479    42  
17682  EntityORGANIZATION  2021-03-30      811668288     13.730859    34  
17683  EntityORGANIZATION  2021-03-16      671921280     14.967183    37  
17684  EntityORGANIZATION  2021-04-03      548577984     15.510063    37  

[17685 rows x 13 columns]

### Did it pick up the Ever Given?
yes! when the story broke

In [171]:
anoms[anoms['stringVal'].str.contains("Ever Given")] #detected anomolies on Ever Given

stringVal                 eventTime  numMentions  is_anomaly  \
12053  Ever Given 2021-03-28 00:00:00+00:00   20261150.0        True   
12054  Ever Given 2021-03-29 00:00:00+00:00   35445880.0       False   
12055  Ever Given 2021-03-27 00:00:00+00:00   16565160.0       False   

        lower_bound   upper_bound  anomaly_probability stringVal_1  \
12053  2.637634e+07  2.812184e+07             1.000000  Ever Given   
12054  3.434226e+07  3.608776e+07             0.506533  Ever Given   
12055  1.569241e+07  1.743791e+07             0.000000  Ever Given   

              name eventTime_1  numMentions_1  avgMagnitude  rank  
12053  EntityOTHER  2021-03-28       20261150      9.883846   248  
12054  EntityOTHER  2021-03-29       35445880      9.474372   200  
12055  EntityOTHER  2021-03-27       16565160      9.774194   287

## Look at anomaly charts by type

In [183]:


def create_entity_count_charts_color(data, filter_terms, only_anom=False, category=None):
    
    if only_anom:
        filtered = anoms[data.is_anomaly == True]
        filtered = filtered[filtered.avgMagnitude > 9]
        filtered_terms = set(filtered.stringVal)
        data = data[data.stringVal.str.contains("|".join(filtered_terms))]
    
    chart_title = f"Anomalies by num mentions"
    if category is not None:
        data = data[data.name == category]
        chart_title = f"Anomalies by num mentions for {category}"
    
    
    if filter_terms is not None:
        data = data[data.stringVal.str.contains('|'.join(filter_terms))]
    #data['eventTime'] = data['eventTime'].astype('datetime64[ns]')

    anomaly_chart = alt.Chart(data).mark_point().encode(
    x={"field": "eventTime", 'type': 'temporal', 'stack': None},
    y={'field': 'numMentions', 'type': 'quantitative', 'stack': None},
    tooltip=['eventTime','numMentions','is_anomaly', 'anomaly_probability', 'stringVal','avgMagnitude'],
    size='is_anomaly',
		).properties(
        height=HEIGHT,
        width=WIDTH*2
    ).interactive()
    
    line_chart = alt.Chart(data).mark_line().encode(
    x={"field": "eventTime", 'type': 'temporal', 'stack': None},
    y={'field': 'numMentions', 'type': 'quantitative', 'stack': None},
    tooltip=['eventTime','numMentions','is_anomaly', 'anomaly_probability', 'stringVal','avgMagnitude'],
    color='stringVal',
		).properties(
        title=chart_title,
        height=HEIGHT,
        width=WIDTH*2
    ).interactive()
    
    
    return alt.layer(anomaly_chart, line_chart)


create_entity_count_charts_color(anoms, filter_terms=['Ever Given','George Floyd'])

alt.LayerChart(...)

In [184]:
create_entity_count_charts_color(anoms, filter_terms=None, only_anom=True, category='EntityOTHER')

alt.LayerChart(...)

Below we see Prince Phillip appearing on the date of his death April 9, then another anomaly for the funeral on the 17th

Another event is the mandate for vaccines in all 50 states on April 7:

#### 7:03 p.m. ET, April 7, 2021
### All 50 states commit to Biden's April 19 deadline to make Covid-19 vaccines available to all US adults
From CNN’s Ben Tinker and Lauren Mascarenhas

In [185]:
create_entity_count_charts_color(anoms, filter_terms=None, only_anom=True, category='EntityEVENT')

alt.LayerChart(...)

In [186]:
create_entity_count_charts_color(anoms, filter_terms=None, only_anom=True, category='EntityCONSUMER_GOOD')

alt.LayerChart(...)

In [187]:
create_entity_count_charts_color(anoms, filter_terms=None, only_anom=True, category='EntityORGANIZATION')

alt.LayerChart(...)